In [1]:
import pandas as pd
import scipy.stats as stats

from sklearn import metrics, model_selection
from catboost import CatBoostClassifier

In [2]:
df_train_binary_encoding = pd.read_csv('../../Feature_Encoding/data/train_binary_encoding.csv')
df_test_binary_encoding = pd.read_csv('../../Feature_Encoding/data/test_binary_encoding.csv')
train = pd.read_csv('../../Feature_Engineering/data/other-cleaned_train.csv')

In [3]:
def cross_val(model, x_train, y_train):
    score_cross_val = model_selection.cross_val_score(model, x_train, y_train, cv=5)
    print(score_cross_val.mean())

In [4]:
#Realiza busqueda completa combinando los parametros
def catboost(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb = {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.05, 0.1], 'l2_leaf_reg': [0, 1, 5]}    
    catb_gs = model_selection.GridSearchCV(catb_classifier, params_catb, cv=5)
    catb_gs.fit(x_train, y_train)
    catb_best = catb_gs.best_estimator_
    print(catb_gs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [5]:
#Realiza busqueda random dentro de los parametros validos
def catboost2(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb_2={
        'n_estimators':stats.randint(10,500),'learning_rate':stats.uniform(0.01,0.3),
        'subsample':stats.uniform(0.3,0.7),'l2_leaf_reg':[1,5,10],
        'max_depth':[3,10,6],'colsample_bylevel':stats.uniform(0.,0.6)
    }
    
    catb_rs = model_selection.RandomizedSearchCV(CatBoostClassifier(),
                          param_distributions=params_catb_2,
                          cv=2,
                          scoring='neg_log_loss',
                          verbose=1,
                          n_iter=200)
    
    catb_rs.fit(x_train, y_train)
    catb_best = catb_rs.best_estimator_
    print(catb_rs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [6]:
def test_model(model, x_test, y_test):
    predictions = model.predict_proba(x_test)[:,1]
    logloss = metrics.log_loss(y_test, predictions)
    accuracy = metrics.accuracy_score(y_test, predictions.round())
    print("Accuracy: %.2f%%, Logloss: %.2f" % (accuracy*100.0, logloss))

In [7]:
y = train.Target
x_train_binary_encoding, x_validation_binary_encoding, y_train_binary_encoding, y_validation_binary_encoding = model_selection.train_test_split(df_train_binary_encoding, y, test_size=0.3, stratify=y)

## Binary encoding

In [8]:
catboost_binary_encoding = catboost(x_train_binary_encoding, y_train_binary_encoding, x_validation_binary_encoding, y_validation_binary_encoding)
test_model(catboost_binary_encoding,x_validation_binary_encoding,y_validation_binary_encoding)
cross_val(catboost_binary_encoding, x_train_binary_encoding, y_train_binary_encoding)

0:	learn: 0.6855510	total: 188ms	remaining: 9.23s
1:	learn: 0.6795063	total: 203ms	remaining: 4.88s
2:	learn: 0.6721671	total: 212ms	remaining: 3.33s
3:	learn: 0.6641760	total: 220ms	remaining: 2.53s
4:	learn: 0.6570669	total: 227ms	remaining: 2.04s
5:	learn: 0.6498512	total: 233ms	remaining: 1.71s
6:	learn: 0.6424555	total: 240ms	remaining: 1.47s
7:	learn: 0.6362623	total: 246ms	remaining: 1.29s
8:	learn: 0.6305974	total: 253ms	remaining: 1.15s
9:	learn: 0.6244473	total: 259ms	remaining: 1.04s
10:	learn: 0.6200736	total: 266ms	remaining: 943ms
11:	learn: 0.6151242	total: 272ms	remaining: 863ms
12:	learn: 0.6104112	total: 279ms	remaining: 794ms
13:	learn: 0.6058709	total: 286ms	remaining: 734ms
14:	learn: 0.6010918	total: 292ms	remaining: 681ms
15:	learn: 0.5965361	total: 298ms	remaining: 634ms
16:	learn: 0.5923035	total: 305ms	remaining: 592ms
17:	learn: 0.5871029	total: 311ms	remaining: 553ms
18:	learn: 0.5820531	total: 318ms	remaining: 519ms
19:	learn: 0.5779983	total: 324ms	remaini

21:	learn: 0.5699904	total: 228ms	remaining: 290ms
22:	learn: 0.5650576	total: 237ms	remaining: 278ms
23:	learn: 0.5613071	total: 248ms	remaining: 268ms
24:	learn: 0.5577297	total: 255ms	remaining: 255ms
25:	learn: 0.5539139	total: 262ms	remaining: 242ms
26:	learn: 0.5506290	total: 270ms	remaining: 230ms
27:	learn: 0.5470559	total: 276ms	remaining: 217ms
28:	learn: 0.5432490	total: 283ms	remaining: 205ms
29:	learn: 0.5400553	total: 290ms	remaining: 193ms
30:	learn: 0.5362271	total: 296ms	remaining: 182ms
31:	learn: 0.5322351	total: 303ms	remaining: 170ms
32:	learn: 0.5287519	total: 310ms	remaining: 160ms
33:	learn: 0.5257918	total: 316ms	remaining: 149ms
34:	learn: 0.5222357	total: 323ms	remaining: 138ms
35:	learn: 0.5186087	total: 330ms	remaining: 128ms
36:	learn: 0.5157984	total: 336ms	remaining: 118ms
37:	learn: 0.5130185	total: 343ms	remaining: 108ms
38:	learn: 0.5100064	total: 349ms	remaining: 98.5ms
39:	learn: 0.5074293	total: 356ms	remaining: 89ms
40:	learn: 0.5050953	total: 363

87:	learn: 0.4195584	total: 611ms	remaining: 83.3ms
88:	learn: 0.4183368	total: 620ms	remaining: 76.6ms
89:	learn: 0.4173464	total: 630ms	remaining: 70.1ms
90:	learn: 0.4154111	total: 637ms	remaining: 63ms
91:	learn: 0.4142487	total: 644ms	remaining: 56ms
92:	learn: 0.4127165	total: 651ms	remaining: 49ms
93:	learn: 0.4116658	total: 657ms	remaining: 42ms
94:	learn: 0.4106653	total: 664ms	remaining: 34.9ms
95:	learn: 0.4095162	total: 671ms	remaining: 27.9ms
96:	learn: 0.4081677	total: 677ms	remaining: 20.9ms
97:	learn: 0.4071351	total: 684ms	remaining: 14ms
98:	learn: 0.4061244	total: 691ms	remaining: 6.98ms
99:	learn: 0.4053213	total: 697ms	remaining: 0us
0:	learn: 0.6849191	total: 8.28ms	remaining: 819ms
1:	learn: 0.6762923	total: 16.5ms	remaining: 808ms
2:	learn: 0.6700773	total: 24.8ms	remaining: 801ms
3:	learn: 0.6626988	total: 33ms	remaining: 793ms
4:	learn: 0.6556540	total: 41.2ms	remaining: 783ms
5:	learn: 0.6497872	total: 49.5ms	remaining: 776ms
6:	learn: 0.6421699	total: 57.8ms

57:	learn: 0.4644265	total: 412ms	remaining: 298ms
58:	learn: 0.4625568	total: 421ms	remaining: 293ms
59:	learn: 0.4607685	total: 429ms	remaining: 286ms
60:	learn: 0.4582157	total: 437ms	remaining: 279ms
61:	learn: 0.4566172	total: 443ms	remaining: 272ms
62:	learn: 0.4543640	total: 450ms	remaining: 265ms
63:	learn: 0.4527286	total: 457ms	remaining: 257ms
64:	learn: 0.4507307	total: 464ms	remaining: 250ms
65:	learn: 0.4479671	total: 471ms	remaining: 243ms
66:	learn: 0.4467171	total: 478ms	remaining: 235ms
67:	learn: 0.4452543	total: 485ms	remaining: 228ms
68:	learn: 0.4437997	total: 492ms	remaining: 221ms
69:	learn: 0.4422135	total: 498ms	remaining: 214ms
70:	learn: 0.4405957	total: 505ms	remaining: 206ms
71:	learn: 0.4391330	total: 512ms	remaining: 199ms
72:	learn: 0.4376581	total: 519ms	remaining: 192ms
73:	learn: 0.4359329	total: 525ms	remaining: 185ms
74:	learn: 0.4345733	total: 532ms	remaining: 177ms
75:	learn: 0.4332987	total: 539ms	remaining: 170ms
76:	learn: 0.4319283	total: 546

27:	learn: 0.5449232	total: 206ms	remaining: 531ms
28:	learn: 0.5412074	total: 223ms	remaining: 546ms
29:	learn: 0.5378501	total: 230ms	remaining: 536ms
30:	learn: 0.5347008	total: 236ms	remaining: 526ms
31:	learn: 0.5305783	total: 243ms	remaining: 517ms
32:	learn: 0.5273187	total: 250ms	remaining: 507ms
33:	learn: 0.5242870	total: 256ms	remaining: 498ms
34:	learn: 0.5210500	total: 263ms	remaining: 488ms
35:	learn: 0.5173247	total: 269ms	remaining: 479ms
36:	learn: 0.5141214	total: 276ms	remaining: 470ms
37:	learn: 0.5112655	total: 283ms	remaining: 461ms
38:	learn: 0.5080755	total: 289ms	remaining: 453ms
39:	learn: 0.5052802	total: 296ms	remaining: 444ms
40:	learn: 0.5025070	total: 302ms	remaining: 435ms
41:	learn: 0.4997948	total: 309ms	remaining: 427ms
42:	learn: 0.4975284	total: 315ms	remaining: 418ms
43:	learn: 0.4949695	total: 322ms	remaining: 410ms
44:	learn: 0.4929088	total: 329ms	remaining: 402ms
45:	learn: 0.4907045	total: 335ms	remaining: 394ms
46:	learn: 0.4880930	total: 342

...

26:	learn: 0.3146006	total: 216ms	remaining: 1.38s
27:	learn: 0.3115886	total: 223ms	remaining: 1.37s
28:	learn: 0.3092675	total: 230ms	remaining: 1.35s
29:	learn: 0.3071134	total: 237ms	remaining: 1.34s
30:	learn: 0.3039314	total: 243ms	remaining: 1.32s
31:	learn: 0.3014163	total: 249ms	remaining: 1.31s
32:	learn: 0.2986435	total: 256ms	remaining: 1.29s
33:	learn: 0.2964817	total: 263ms	remaining: 1.28s
34:	learn: 0.2937311	total: 270ms	remaining: 1.27s
35:	learn: 0.2905774	total: 277ms	remaining: 1.26s
36:	learn: 0.2863245	total: 284ms	remaining: 1.25s
37:	learn: 0.2835827	total: 290ms	remaining: 1.24s
38:	learn: 0.2817254	total: 297ms	remaining: 1.22s
39:	learn: 0.2796130	total: 303ms	remaining: 1.21s
40:	learn: 0.2769695	total: 310ms	remaining: 1.2s
41:	learn: 0.2755309	total: 317ms	remaining: 1.19s
42:	learn: 0.2732008	total: 324ms	remaining: 1.18s
43:	learn: 0.2713014	total: 331ms	remaining: 1.17s
44:	learn: 0.2694861	total: 338ms	remaining: 1.16s
45:	learn: 0.2676677	total: 345m

196:	learn: 0.1148368	total: 1.43s	remaining: 21.7ms
197:	learn: 0.1142192	total: 1.43s	remaining: 14.5ms
198:	learn: 0.1137676	total: 1.44s	remaining: 7.24ms
199:	learn: 0.1133355	total: 1.45s	remaining: 0us
0:	learn: 0.6270920	total: 8.47ms	remaining: 1.69s
1:	learn: 0.5722051	total: 16.7ms	remaining: 1.65s
2:	learn: 0.5350826	total: 30.1ms	remaining: 1.98s
3:	learn: 0.5047588	total: 38.9ms	remaining: 1.9s
4:	learn: 0.4778737	total: 46.7ms	remaining: 1.82s
5:	learn: 0.4516888	total: 55.1ms	remaining: 1.78s
6:	learn: 0.4357346	total: 62.8ms	remaining: 1.73s
7:	learn: 0.4200339	total: 70.6ms	remaining: 1.7s
8:	learn: 0.4097217	total: 78.8ms	remaining: 1.67s
9:	learn: 0.3998451	total: 89.5ms	remaining: 1.7s
10:	learn: 0.3908644	total: 99.7ms	remaining: 1.71s
11:	learn: 0.3796389	total: 109ms	remaining: 1.71s
12:	learn: 0.3743967	total: 118ms	remaining: 1.69s
13:	learn: 0.3686736	total: 126ms	remaining: 1.67s
14:	learn: 0.3602244	total: 133ms	remaining: 1.64s
15:	learn: 0.3552334	total: 

167:	learn: 0.1298750	total: 1.44s	remaining: 273ms
168:	learn: 0.1292423	total: 1.44s	remaining: 265ms
169:	learn: 0.1284800	total: 1.45s	remaining: 256ms
170:	learn: 0.1275147	total: 1.46s	remaining: 247ms
171:	learn: 0.1266945	total: 1.47s	remaining: 239ms
172:	learn: 0.1260063	total: 1.47s	remaining: 230ms
173:	learn: 0.1254018	total: 1.48s	remaining: 221ms
174:	learn: 0.1246252	total: 1.49s	remaining: 212ms
175:	learn: 0.1239030	total: 1.49s	remaining: 204ms
176:	learn: 0.1233553	total: 1.5s	remaining: 195ms
177:	learn: 0.1226199	total: 1.51s	remaining: 187ms
178:	learn: 0.1220070	total: 1.52s	remaining: 178ms
179:	learn: 0.1212625	total: 1.53s	remaining: 170ms
180:	learn: 0.1204467	total: 1.53s	remaining: 161ms
181:	learn: 0.1197092	total: 1.54s	remaining: 153ms
182:	learn: 0.1189572	total: 1.55s	remaining: 144ms
183:	learn: 0.1183653	total: 1.56s	remaining: 135ms
184:	learn: 0.1179523	total: 1.56s	remaining: 127ms
185:	learn: 0.1172366	total: 1.58s	remaining: 119ms
186:	learn: 0

149:	learn: 0.1482799	total: 1.26s	remaining: 419ms
150:	learn: 0.1476358	total: 1.26s	remaining: 411ms
151:	learn: 0.1471318	total: 1.27s	remaining: 402ms
152:	learn: 0.1464423	total: 1.28s	remaining: 393ms
153:	learn: 0.1460895	total: 1.29s	remaining: 385ms
154:	learn: 0.1454628	total: 1.29s	remaining: 376ms
155:	learn: 0.1443596	total: 1.3s	remaining: 367ms
156:	learn: 0.1428332	total: 1.31s	remaining: 359ms
157:	learn: 0.1419192	total: 1.32s	remaining: 350ms
158:	learn: 0.1409599	total: 1.32s	remaining: 342ms
159:	learn: 0.1401992	total: 1.33s	remaining: 333ms
160:	learn: 0.1394166	total: 1.34s	remaining: 325ms
161:	learn: 0.1388449	total: 1.35s	remaining: 316ms
162:	learn: 0.1381157	total: 1.35s	remaining: 308ms
163:	learn: 0.1374594	total: 1.36s	remaining: 299ms
164:	learn: 0.1368862	total: 1.37s	remaining: 291ms
165:	learn: 0.1360435	total: 1.38s	remaining: 282ms
166:	learn: 0.1353112	total: 1.39s	remaining: 274ms
167:	learn: 0.1345474	total: 1.39s	remaining: 266ms
168:	learn: 0

137:	learn: 0.1568931	total: 1.04s	remaining: 466ms
138:	learn: 0.1561490	total: 1.04s	remaining: 459ms
139:	learn: 0.1549409	total: 1.05s	remaining: 451ms
140:	learn: 0.1543265	total: 1.06s	remaining: 443ms
141:	learn: 0.1532420	total: 1.07s	remaining: 435ms
142:	learn: 0.1522895	total: 1.07s	remaining: 428ms
143:	learn: 0.1515894	total: 1.08s	remaining: 420ms
144:	learn: 0.1509430	total: 1.09s	remaining: 412ms
145:	learn: 0.1503166	total: 1.09s	remaining: 405ms
146:	learn: 0.1494468	total: 1.1s	remaining: 397ms
147:	learn: 0.1486367	total: 1.11s	remaining: 390ms
148:	learn: 0.1478047	total: 1.12s	remaining: 382ms
149:	learn: 0.1470844	total: 1.12s	remaining: 375ms
150:	learn: 0.1465177	total: 1.13s	remaining: 367ms
151:	learn: 0.1457938	total: 1.14s	remaining: 360ms
152:	learn: 0.1449525	total: 1.15s	remaining: 352ms
153:	learn: 0.1443065	total: 1.15s	remaining: 345ms
154:	learn: 0.1430953	total: 1.16s	remaining: 337ms
155:	learn: 0.1423299	total: 1.17s	remaining: 330ms
156:	learn: 0

In [9]:
catboost_binary_encoding = catboost2(x_train_binary_encoding, y_train_binary_encoding, x_validation_binary_encoding, y_validation_binary_encoding)
test_model(catboost_binary_encoding,x_validation_binary_encoding,y_validation_binary_encoding)
cross_val(catboost_binary_encoding, x_train_binary_encoding, y_train_binary_encoding)

Fitting 2 folds for each of 200 candidates, totalling 400 fits
0:	learn: 0.5558918	total: 136ms	remaining: 41.9s
1:	learn: 0.4723037	total: 205ms	remaining: 31.3s
2:	learn: 0.4171673	total: 271ms	remaining: 27.5s
3:	learn: 0.3852030	total: 356ms	remaining: 27s
4:	learn: 0.3646970	total: 418ms	remaining: 25.3s
5:	learn: 0.3406359	total: 476ms	remaining: 24s
6:	learn: 0.3256029	total: 543ms	remaining: 23.3s
7:	learn: 0.3098442	total: 602ms	remaining: 22.6s
8:	learn: 0.2976032	total: 661ms	remaining: 22s
9:	learn: 0.2848515	total: 719ms	remaining: 21.4s
10:	learn: 0.2749393	total: 775ms	remaining: 20.9s
11:	learn: 0.2642439	total: 834ms	remaining: 20.6s
12:	learn: 0.2581296	total: 894ms	remaining: 20.3s
13:	learn: 0.2527738	total: 953ms	remaining: 20s
14:	learn: 0.2438180	total: 1.02s	remaining: 19.9s
15:	learn: 0.2353566	total: 1.08s	remaining: 19.8s
16:	learn: 0.2315633	total: 1.14s	remaining: 19.5s
17:	learn: 0.2257777	total: 1.2s	remaining: 19.4s
18:	learn: 0.2215407	total: 1.26s	rema

160:	learn: 0.0292008	total: 10.5s	remaining: 9.61s
161:	learn: 0.0288233	total: 10.6s	remaining: 9.54s
162:	learn: 0.0286124	total: 10.6s	remaining: 9.47s
163:	learn: 0.0283272	total: 10.7s	remaining: 9.4s
164:	learn: 0.0281169	total: 10.8s	remaining: 9.33s
165:	learn: 0.0278568	total: 10.8s	remaining: 9.27s
166:	learn: 0.0276236	total: 10.9s	remaining: 9.2s
167:	learn: 0.0272581	total: 11s	remaining: 9.13s
168:	learn: 0.0270117	total: 11s	remaining: 9.06s
169:	learn: 0.0267869	total: 11.1s	remaining: 9.01s
170:	learn: 0.0266726	total: 11.2s	remaining: 8.95s
171:	learn: 0.0264702	total: 11.2s	remaining: 8.89s
172:	learn: 0.0262208	total: 11.3s	remaining: 8.84s
173:	learn: 0.0259672	total: 11.4s	remaining: 8.77s
174:	learn: 0.0257339	total: 11.4s	remaining: 8.7s
175:	learn: 0.0255263	total: 11.5s	remaining: 8.63s
176:	learn: 0.0252756	total: 11.6s	remaining: 8.56s
177:	learn: 0.0250633	total: 11.6s	remaining: 8.49s
178:	learn: 0.0248597	total: 11.7s	remaining: 8.42s
179:	learn: 0.02477

12:	learn: 0.2592941	total: 758ms	remaining: 17.2s
13:	learn: 0.2529311	total: 816ms	remaining: 17.1s
14:	learn: 0.2435447	total: 874ms	remaining: 17.1s
15:	learn: 0.2356282	total: 939ms	remaining: 17.1s
16:	learn: 0.2276646	total: 997ms	remaining: 17.1s
17:	learn: 0.2199748	total: 1.06s	remaining: 17s
18:	learn: 0.2136270	total: 1.12s	remaining: 17s
19:	learn: 0.2110901	total: 1.18s	remaining: 16.9s
20:	learn: 0.2037604	total: 1.24s	remaining: 16.9s
21:	learn: 0.1978947	total: 1.3s	remaining: 16.9s
22:	learn: 0.1946914	total: 1.37s	remaining: 16.9s
23:	learn: 0.1861390	total: 1.43s	remaining: 16.9s
24:	learn: 0.1814132	total: 1.49s	remaining: 16.9s
25:	learn: 0.1784672	total: 1.55s	remaining: 16.8s
26:	learn: 0.1750522	total: 1.61s	remaining: 16.7s
27:	learn: 0.1712700	total: 1.67s	remaining: 16.7s
28:	learn: 0.1682135	total: 1.73s	remaining: 16.6s
29:	learn: 0.1644788	total: 1.79s	remaining: 16.6s
30:	learn: 0.1610830	total: 1.85s	remaining: 16.5s
31:	learn: 0.1588243	total: 1.91s	re

174:	learn: 0.0254131	total: 11s	remaining: 8.33s
175:	learn: 0.0251195	total: 11s	remaining: 8.26s
176:	learn: 0.0249211	total: 11.1s	remaining: 8.2s
177:	learn: 0.0246644	total: 11.1s	remaining: 8.13s
178:	learn: 0.0244471	total: 11.2s	remaining: 8.07s
179:	learn: 0.0241451	total: 11.3s	remaining: 8.01s
180:	learn: 0.0238411	total: 11.3s	remaining: 7.94s
181:	learn: 0.0236806	total: 11.4s	remaining: 7.88s
182:	learn: 0.0235731	total: 11.5s	remaining: 7.83s
183:	learn: 0.0234139	total: 11.5s	remaining: 7.76s
184:	learn: 0.0231359	total: 11.6s	remaining: 7.7s
185:	learn: 0.0229290	total: 11.6s	remaining: 7.64s
186:	learn: 0.0227099	total: 11.7s	remaining: 7.58s
187:	learn: 0.0224609	total: 11.8s	remaining: 7.52s
188:	learn: 0.0222938	total: 11.8s	remaining: 7.45s
189:	learn: 0.0220165	total: 11.9s	remaining: 7.39s
190:	learn: 0.0217327	total: 12s	remaining: 7.33s
191:	learn: 0.0217326	total: 12s	remaining: 7.26s
192:	learn: 0.0216335	total: 12.1s	remaining: 7.2s
193:	learn: 0.0214246	t

40:	learn: 0.3205565	total: 200ms	remaining: 1.7s
41:	learn: 0.3182607	total: 206ms	remaining: 1.7s
42:	learn: 0.3163448	total: 211ms	remaining: 1.69s
43:	learn: 0.3149707	total: 215ms	remaining: 1.68s
44:	learn: 0.3129877	total: 220ms	remaining: 1.68s
45:	learn: 0.3105635	total: 224ms	remaining: 1.67s
46:	learn: 0.3085219	total: 229ms	remaining: 1.66s
47:	learn: 0.3071524	total: 233ms	remaining: 1.65s
48:	learn: 0.3057908	total: 238ms	remaining: 1.65s
49:	learn: 0.3042195	total: 242ms	remaining: 1.64s
50:	learn: 0.3032445	total: 247ms	remaining: 1.63s
51:	learn: 0.3022808	total: 252ms	remaining: 1.63s
52:	learn: 0.3009010	total: 256ms	remaining: 1.62s
53:	learn: 0.2997201	total: 260ms	remaining: 1.61s
54:	learn: 0.2983577	total: 264ms	remaining: 1.6s
55:	learn: 0.2968743	total: 269ms	remaining: 1.59s
56:	learn: 0.2946953	total: 275ms	remaining: 1.59s
57:	learn: 0.2938230	total: 279ms	remaining: 1.58s
58:	learn: 0.2917448	total: 283ms	remaining: 1.58s
59:	learn: 0.2901764	total: 288ms	

...

286:	learn: 0.0838792	total: 21.6s	remaining: 13.9s
287:	learn: 0.0836451	total: 21.7s	remaining: 13.8s
288:	learn: 0.0833702	total: 21.7s	remaining: 13.8s
289:	learn: 0.0829593	total: 21.8s	remaining: 13.7s
290:	learn: 0.0828188	total: 21.9s	remaining: 13.6s
291:	learn: 0.0823979	total: 22s	remaining: 13.5s
292:	learn: 0.0821826	total: 22s	remaining: 13.5s
293:	learn: 0.0819521	total: 22.1s	remaining: 13.4s
294:	learn: 0.0813880	total: 22.2s	remaining: 13.3s
295:	learn: 0.0812216	total: 22.3s	remaining: 13.2s
296:	learn: 0.0807668	total: 22.3s	remaining: 13.2s
297:	learn: 0.0805474	total: 22.4s	remaining: 13.1s
298:	learn: 0.0802761	total: 22.5s	remaining: 13s
299:	learn: 0.0798302	total: 22.6s	remaining: 12.9s
300:	learn: 0.0795411	total: 22.6s	remaining: 12.9s
301:	learn: 0.0791681	total: 22.7s	remaining: 12.8s
302:	learn: 0.0789505	total: 22.8s	remaining: 12.7s
303:	learn: 0.0788269	total: 22.9s	remaining: 12.6s
304:	learn: 0.0785411	total: 22.9s	remaining: 12.6s
305:	learn: 0.0782

445:	learn: 0.0494714	total: 33.5s	remaining: 1.95s
446:	learn: 0.0492829	total: 33.5s	remaining: 1.87s
447:	learn: 0.0490569	total: 33.6s	remaining: 1.8s
448:	learn: 0.0489491	total: 33.7s	remaining: 1.72s
449:	learn: 0.0487612	total: 33.7s	remaining: 1.65s
450:	learn: 0.0485560	total: 33.8s	remaining: 1.57s
451:	learn: 0.0484082	total: 33.9s	remaining: 1.5s
452:	learn: 0.0481689	total: 34s	remaining: 1.42s
453:	learn: 0.0480216	total: 34s	remaining: 1.35s
454:	learn: 0.0479160	total: 34.1s	remaining: 1.27s
455:	learn: 0.0477600	total: 34.2s	remaining: 1.2s
456:	learn: 0.0476571	total: 34.3s	remaining: 1.12s
457:	learn: 0.0475394	total: 34.3s	remaining: 1.05s
458:	learn: 0.0474209	total: 34.4s	remaining: 975ms
459:	learn: 0.0473117	total: 34.5s	remaining: 900ms
460:	learn: 0.0471888	total: 34.6s	remaining: 825ms
461:	learn: 0.0470307	total: 34.6s	remaining: 750ms
462:	learn: 0.0468763	total: 34.7s	remaining: 675ms
463:	learn: 0.0467772	total: 34.8s	remaining: 600ms
464:	learn: 0.04670

136:	learn: 0.1548127	total: 10.4s	remaining: 25.4s
137:	learn: 0.1543006	total: 10.5s	remaining: 25.3s
138:	learn: 0.1540131	total: 10.5s	remaining: 25.2s
139:	learn: 0.1530783	total: 10.6s	remaining: 25.2s
140:	learn: 0.1515817	total: 10.7s	remaining: 25.1s
141:	learn: 0.1510980	total: 10.8s	remaining: 25s
142:	learn: 0.1503016	total: 10.8s	remaining: 24.9s
143:	learn: 0.1493621	total: 10.9s	remaining: 24.9s
144:	learn: 0.1486950	total: 11s	remaining: 24.8s
145:	learn: 0.1481161	total: 11.1s	remaining: 24.7s
146:	learn: 0.1476875	total: 11.1s	remaining: 24.6s
147:	learn: 0.1474342	total: 11.2s	remaining: 24.5s
148:	learn: 0.1470126	total: 11.3s	remaining: 24.4s
149:	learn: 0.1462479	total: 11.3s	remaining: 24.4s
150:	learn: 0.1453054	total: 11.4s	remaining: 24.3s
151:	learn: 0.1448456	total: 11.5s	remaining: 24.2s
152:	learn: 0.1445240	total: 11.6s	remaining: 24.1s
153:	learn: 0.1434019	total: 11.7s	remaining: 24.1s
154:	learn: 0.1426265	total: 11.7s	remaining: 24s
155:	learn: 0.1418

295:	learn: 0.0806881	total: 22.4s	remaining: 13.3s
296:	learn: 0.0803620	total: 22.4s	remaining: 13.2s
297:	learn: 0.0801846	total: 22.5s	remaining: 13.1s
298:	learn: 0.0798168	total: 22.6s	remaining: 13.1s
299:	learn: 0.0796486	total: 22.7s	remaining: 13s
300:	learn: 0.0794445	total: 22.7s	remaining: 12.9s
301:	learn: 0.0792964	total: 22.8s	remaining: 12.8s
302:	learn: 0.0791393	total: 22.9s	remaining: 12.8s
303:	learn: 0.0789365	total: 23s	remaining: 12.7s
304:	learn: 0.0786496	total: 23.1s	remaining: 12.6s
305:	learn: 0.0784915	total: 23.1s	remaining: 12.6s
306:	learn: 0.0783581	total: 23.2s	remaining: 12.5s
307:	learn: 0.0782177	total: 23.3s	remaining: 12.4s
308:	learn: 0.0779521	total: 23.4s	remaining: 12.3s
309:	learn: 0.0777755	total: 23.4s	remaining: 12.2s
310:	learn: 0.0775106	total: 23.5s	remaining: 12.2s
311:	learn: 0.0773427	total: 23.6s	remaining: 12.1s
312:	learn: 0.0769550	total: 23.7s	remaining: 12s
313:	learn: 0.0765577	total: 23.7s	remaining: 11.9s
314:	learn: 0.0763

454:	learn: 0.0493247	total: 34.3s	remaining: 1.28s
455:	learn: 0.0491882	total: 34.4s	remaining: 1.21s
456:	learn: 0.0489640	total: 34.4s	remaining: 1.13s
457:	learn: 0.0488686	total: 34.5s	remaining: 1.05s
458:	learn: 0.0487289	total: 34.6s	remaining: 979ms
459:	learn: 0.0486153	total: 34.6s	remaining: 904ms
460:	learn: 0.0484461	total: 34.7s	remaining: 829ms
461:	learn: 0.0483012	total: 34.8s	remaining: 753ms
462:	learn: 0.0481992	total: 34.9s	remaining: 678ms
463:	learn: 0.0480275	total: 35s	remaining: 603ms
464:	learn: 0.0478805	total: 35s	remaining: 527ms
465:	learn: 0.0478160	total: 35.1s	remaining: 452ms
466:	learn: 0.0477370	total: 35.2s	remaining: 377ms
467:	learn: 0.0476563	total: 35.3s	remaining: 301ms
468:	learn: 0.0475027	total: 35.3s	remaining: 226ms
469:	learn: 0.0473784	total: 35.4s	remaining: 151ms
470:	learn: 0.0472205	total: 35.5s	remaining: 75.3ms
471:	learn: 0.0471034	total: 35.5s	remaining: 0us
0.9153833457569567


In [10]:
y_pred = catboost_binary_encoding.predict_proba(df_test_binary_encoding)[:,1]
submission_catboost = pd.DataFrame(data={'Opportunity_ID':df_test_binary_encoding['Opportunity_ID'], 'Target': y_pred})
submission_catboost = submission_catboost.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_catboost.to_csv('../submits/binary_catboost.csv', index=False)